# Esercitazioni
In questo quaderno proviamo a mettere in atto insieme quanto abbiamo appreso per costruire uno spettro ed effettuare una calibrazione. Questa parte in particolare vi sarà richiesto di farla durante l'attività di spettroscopia gamma, quindi può essere utile avere un'idea di come approciare il problema ed avere qualcosa di già pronto all'uso :)

Come al solito, l'analisi verrà effettuata col pitone.

## Step 0: import dei moduli necessari

Iniziamo caricando i moduli necessari: non preoccupatevi se ve ne scordate qualcuno che vi servirà in seguito, si può sempre tornare qui ad aggiungerla oppure caricarla laddove ci serve. Per mantenere il codice più ordinato, può essere buona norma caricarle qui.

In [1]:
# Codice per caricare i moduli necessari


## Step 1: load dei dati

I dati che da utilizzare sono contenuti nel file [`run020752.dat`](https://scarsi.web.cern.ch/INSULAB/LAB4/run020752.dat): si tratta di un file ASCII (che vi lascio l'onore di aprire da soli) costituito da 5 colonne: la prima contiene il tempo UNIX, mentre le altre 4 il valore del massimo della waveform riferito a 4 diversi canali. Voi dovrete utilizzare i dati provenienti dal primo canale, ovvero contenuti nella colonna...?

In [2]:
# Codice per caricare i dati


In [3]:
# Codice per visualizzare schematicamente informazioni sui dati


## Step 2: costruzione e visualizzazione dell'istogramma

Come abbiamo visto, a noi interessa la distribuzione di questi valori: procediamo quindi alla costruzione di un istogramma ed alla sua visualizzazione. L'ADC, ovvero lo strumento che campiona la forma d'onda ha una risoluzione a 12 bit, quindi il maggior numero che ci può restituire è $2^{12}=$..? Casomai comparissero valori più elevati, che si fa?

In [4]:
# Codice per costruire l'istogramma


In [5]:
# Codice per visualizzare l'istogramma


Una riflessione finale:
Abbiamo fatto il taglio sull'istogramma già costruito, in poche parole visualizziamo solamente una porzione
dell'istogramma costruito. Poiché ci sono fondati motivi teorici per fissare un limite massimo, sarebbe buona
norma mettere il range sull'istogramma da costruire.
In questo esempio ho aggirato il problema facendo mooolti bin

## Step 3: fit dei picchi

Una volta costruito l'istogramma, vogliamo effettuare il fit dei picchi: in particolare vogliamo trovare la $x$ del massimo e il corrispondente errore: effettuiamo quindi il fit con una funzione...?

Notare in particolare come i picchi non siano centrati sullo 0 ma abbiano un offset verticale: sarà opportuno tenerne conto. Se il passaggio precedente è stato effettuato correttamente può sembrare che siano montati su una retta decrescente: attenzione a non farsi ingannare dalle impostazioni degli assi

I picchi da fittare sono i primi 7, che hanno energie 77, 185, 241, 295, 351, 609 e 1120 keV. (Il secondo picco nell'immagine sottostante compare a 186/187, nel logbook fornito era dato a 185. In ogni caso non fa tutta sta gran differenza...)

![](./226Ra.jpg)

Si tratta di fit un po' delicati da far convergere, serve un po' di pazienza: per aiutarsi a stimare gli starting points può essere utile ricorrere al seguente magic command `%matplotlib qt` che consente di aprire il plot in una finestra grafica esterna, e dove muovendosi col puntatore si possono visualizzare le coordinate. Per visualizzare i plot nel modo usuale, esiste il magic command `%matplotlib inline`. 

In [6]:
# Definiamo la funzione di fit


In [7]:
# Codice per fare e visualizzare i fit


## Step 4: ottenimento dei valori estratti dal fit

Dopo aver effettuato il fit è importante ottenere i parametri risultanti dal fit, in particolare ci interessa ottenere $\mu$ e $\sigma$ delle gaussiane con i relativi errori. I parametri si trovano direttamente in `popt`, mentre `pcov` costituisce la matrice delle covarianze. Sulla diagonale si trovano le varianze, ovvero il quadrato dell'incertezza.

Inoltre, essendo la gaussiana $$\dfrac{1}{\sigma\,\sqrt{2\pi}}\,e^{-\dfrac{(x-\mu)^2}{2\sigma^2}}$$
normalizzata, ovvero di area unitaria, il prefattore $a$ rappresenta l'area della gaussiana.

In [8]:
# Codice per ottenere parametri ed errori


## Step 5: costruzione della retta di calibrazione

A questo punto, sapendo i valori dei picchi in ADC e la corrispondente energia vera, possiamo costruire la **retta di calibrazione**. Per stabilire chi mettere sulle $x$ e chi sulle $y$ chiediamoci chi ha errore e chi assumiamo come esatto. Ricordiamoci inoltre che la retta di calibrazione consente di passare da ADC a keV.

In [9]:
# Codice per fittare la retta di calibrazione


In [10]:
# Codice per plottare la retta di calibrazione


## Step 6: plot dell'istogramma in energia

A questo punto per plottare l'istogramma in energia non ci resta che copiare il codice usato in precedenza, applicando *una certa trasformazione* alle $x$... per ottenere lo spettro della nostra sorgente di $^{226}$Ra.

In [11]:
# Codice per plottare l'istogramma in energie


# Pro tip

Durante l'attività di spettroscopia gamma acquisirete un file per ogni sorgente: piuttosto che aprire ciascun file salvandosi i dati in differenti variabili, può essere comodo automatizzare la procedura. Per ogni evento vengono salvati due differenti files: uno ".dat" che contiene i dati e uno ".log" che contiene alcune informazioni sull'acquisizione.

In una certa cartella ho due sottocartelle:
- PITONE: contiene gli script python
- DATI: contiene i dati acquisiti
Per automatizzare il tutto potrebbe essere conveniente implementare qualcosa del tipo

```python
# Questa lista contiene le varie matrici di dati, ogni matrice è un file
listaMatrici = []
# Questa lista invece contiene 
listaNum = []

# Ciclo su tutti i files nella cartella dati, indietro di un livello ("..")
for e in os.scandir(r"..\DATI"):
    if e.name.split(".")[1] != "dat": continue

    tmp = np.loadtxt(e.path)
    listaMatrici.append(tmp.copy())
    listaNum.append(int(e.name.split(".")[0][-2:]))
    
zipIt = zip(listaNum, range(len(listaNum)))
# Questo dizionario accetta come input il numero di run (in realtà gli ultimi due numeri) e dà come output l'indice progressivo con cui è stato caricato. Non è automaticamente garantito che i dati vengano caricati in ordine alfabetico
myDict = dict(zipIt)
```

Attenzione! È fodnamentale appendere `tmp.copy()` e non semplicemente `tmp`: nel primo caso si appende un nuovo oggetto per ogni file, mentre nel secondo caso si appende sempre lo stesso oggetto (e quindi tutte le matrici sarebbero uguali all'ultimo file aperto). 

Per effettuare la procedura di analisi e fit, anziché costruire manualmente plot ed istogrammi per ciascuna sorgente, ho implementato una funzione la cui firma è
```python
def makeFit(numRun, sogliaMin, sogliaMax, startPars, rangeFit, valVero, sorgente,\
            fig, ax, primoPicco = True):
```
che può essere un utile spunto. Ognuno di voi sceglierà comunque la strategia che più ritiene opportuna. In particolare l'opzione `primoPicco` serve a tener conto di sorgenti che abbiano più picchi (come il caso del $^{226}$Ra che abbiamo visto in questa esercitazione.

# Correlazioni

Se qualcuno volesse divertirsi, utilizzando [questi dati](https://scarsi.web.cern.ch/INSULAB/LAB4/run020252.dat) si possono provare a studiare le correlazioni. I dati sono formattati esattamente come nel caso precedente, solo che vi sono due PMT, connessi ai primi due canali dell'ADC

In [12]:
# Codice per visualizzare le correlazioni


Il significato di questo plot vi sarà sicuramente più chiaro dalla teoria vista a lezione e dall'esperienza relativa in laboratorio.
Senza la pretesa di essere esaustivo, dalla mia relazione:
<blockquote>
Si possono distinguere due bande verticali/orizzontali
in corrispondenza dei picchi fotoelettrici a 511 keV e 1274 keV: il primo
corrisponde al picco di annichilazione, mentre il secondo al fotone emesso dal
decadimento della sorgente. Non si nota un significativo addensamento in prossimità
dell’intersezione a 511 keV in quanto la sorgente era posta davanti ai
due rivelatori, mentre i due fotoni di annichilazione vengono emessi in direzioni
opposte: non risulta quindi possibile rivelare nei due rivelatori i due fotoni emessi
dall’annichilazione, e quando entrambi i rivelatori hanno rivelato un fotone da
511 keV non può che essere un evento casuale, dato dalla rivelazione di un fotone
ciascuno proveniente da due annichilazioni differenti.    
    
Le due bande diagonali rappresentano la situazione
in cui un fotone all’interno di un rivelatore ceda parte della sua energia per
effetto Compton e il fotone Compton, di bassa energia, ceda la rimanente energia
all’altro rivelatore: in questo caso tutta l’energia è stata ceduta, ma ai due
rivelatori vengono di volta in volta ceduti differenti valori.
    
Sotto la diagonale a 511 keV si può ben distinguere il Compton continuum.
Si osservi in particolare come le bande diagonali non raggiungano mai gli assi:
questo si verifica poiché il massimo trasferimento di energia mediante effetto
Compton non coincide col picco fotoelettrico, ed infatti negli spettri la spalla
Compton si trova sempre prima del corrispondente picco fotoelettrico.
</blockquote>

